In [1]:
import os
import glob
import numpy as np
import pandas as pd

import cv2
from PIL import Image
from tqdm.auto import tqdm

/Users/arahjou/Documents/Com_Conda/.conda/lib/python3.11/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


Combining CSV file containing inforamtion about masks and images adresse.

In [2]:
df_train = pd.read_csv("/Users/arahjou/Downloads/uw-madison-gi-tract-image-segmentation/train.csv")
df_train = df_train.sort_values(["id", "class"]).reset_index(drop = True)
df_train["patient"] = df_train.id.apply(lambda x: x.split("_")[0])
df_train["days"] = df_train.id.apply(lambda x: "_".join(x.split("_")[:2]))

all_image_files = sorted(glob.glob("/Users/arahjou/Downloads/uw-madison-gi-tract-image-segmentation/train/*/*/scans/*.png"), key = lambda x: x.split("/")[3] + "_" + x.split("/")[5])
size_x = [int(os.path.basename(_)[:-4].split("_")[-4]) for _ in all_image_files]
size_y = [int(os.path.basename(_)[:-4].split("_")[-3]) for _ in all_image_files]
spacing_x = [float(os.path.basename(_)[:-4].split("_")[-2]) for _ in all_image_files]
spacing_y = [float(os.path.basename(_)[:-4].split("_")[-1]) for _ in all_image_files]
df_train["image_files"] = np.repeat(all_image_files, 3)
df_train["spacing_x"] = np.repeat(spacing_x, 3)
df_train["spacing_y"] = np.repeat(spacing_y, 3)
df_train["size_x"] = np.repeat(size_x, 3)
df_train["size_y"] = np.repeat(size_y, 3)
df_train["slice"] = np.repeat([int(os.path.basename(_)[:-4].split("_")[-5]) for _ in all_image_files], 3)
df_train.head()

id        class segmentation  patient           days  \
0  case101_day20_slice_0001  large_bowel          NaN  case101  case101_day20   
1  case101_day20_slice_0001  small_bowel          NaN  case101  case101_day20   
2  case101_day20_slice_0001      stomach          NaN  case101  case101_day20   
3  case101_day20_slice_0002  large_bowel          NaN  case101  case101_day20   
4  case101_day20_slice_0002  small_bowel          NaN  case101  case101_day20   

                                         image_files  spacing_x  spacing_y  \
0  /Users/arahjou/Downloads/uw-madison-gi-tract-i...        1.5        1.5   
1  /Users/arahjou/Downloads/uw-madison-gi-tract-i...        1.5        1.5   
2  /Users/arahjou/Downloads/uw-madison-gi-tract-i...        1.5        1.5   
3  /Users/arahjou/Downloads/uw-madison-gi-tract-i...        1.5        1.5   
4  /Users/arahjou/Downloads/uw-madison-gi-tract-i...        1.5        1.5   

   size_x  size_y  slice  
0     266     266    131  
1     266     266    131  
2     266     266    131  
3     266     266     32  
4     266     266     32

In [3]:
df = df_train.copy()

Merging relu information for each slid and adding information if a slid contation organ of interest.

In [4]:
df['segmentation'] = df.segmentation.fillna('')
df['rle_len'] = df.segmentation.map(len) # length of each rle mask
#df['mask_path'] = df.mask_path.str.replace('/png/','/np').str.replace('.png','.npy')

df2 = df.groupby(['id'])['segmentation'].agg(list).to_frame().reset_index() # rle list of each id
df2 = df2.merge(df.groupby(['id'])['rle_len'].agg(sum).to_frame().reset_index()) # total length of all rles of each id
df2.head()
df = df.drop(columns=['segmentation', 'class', 'rle_len'])
df = df.groupby(['id']).head(1).reset_index(drop=True)
df = df.merge(df2, on=['id'])
df['empty'] = (df.rle_len==0) # empty masks
df.head()

/var/folders/j5/c5vt47v9695609y1ssl7zjdr0000gn/T/ipykernel_3499/3965821724.py:6: FutureWarning: The provided callable <built-in function sum> is currently using SeriesGroupBy.sum. In a future version of pandas, the provided callable will be used directly. To keep current behavior pass the string "sum" instead.
  df2 = df2.merge(df.groupby(['id'])['rle_len'].agg(sum).to_frame().reset_index()) # total length of all rles of each id


id  patient           days  \
0  case101_day20_slice_0001  case101  case101_day20   
1  case101_day20_slice_0002  case101  case101_day20   
2  case101_day20_slice_0003  case101  case101_day20   
3  case101_day20_slice_0004  case101  case101_day20   
4  case101_day20_slice_0005  case101  case101_day20   

                                         image_files  spacing_x  spacing_y  \
0  /Users/arahjou/Downloads/uw-madison-gi-tract-i...        1.5        1.5   
1  /Users/arahjou/Downloads/uw-madison-gi-tract-i...        1.5        1.5   
2  /Users/arahjou/Downloads/uw-madison-gi-tract-i...        1.5        1.5   
3  /Users/arahjou/Downloads/uw-madison-gi-tract-i...        1.5        1.5   
4  /Users/arahjou/Downloads/uw-madison-gi-tract-i...        1.5        1.5   

   size_x  size_y  slice segmentation  rle_len  empty  
0     266     266    131       [, , ]        0   True  
1     266     266     32       [, , ]        0   True  
2     266     266     84       [, , ]        0   True  
3     266     266     92       [, , ]        0   True  
4     266     266     24       [, , ]        0   True

**Adding an additional colum that divides slide into three classes**

The strategy should be:

1. **Group by 'patient' and 'days'.**
2. **Within each group**:
   - Mark rows before the first occurrence of `empty == False` as 'class_I'.
   - Mark the row where `empty == False` as 'class_II'.
   - Mark the rows after the first `empty == False` as 'class_III'.

Let's implement this strategy in the Python script. I'll modify the script accordingly and apply these rules to each group.

The script has been adjusted according to the new rules you provided:

- Rows before the first occurrence of `empty == False` are classified as 'class_I'.
- The first occurrence of `empty == False` is classified as 'class_II'.
- Rows after this occurrence within the same group are classified as 'class_III'.

The results have been saved to "Change_Adjusted.csv". You can download the updated file from the following link:


Please let me know if there are any more adjustments or additional rules you'd like to apply!

In [5]:
original_df = df.copy()

def classify_group_final(group):
    # Initialize the class column
    group['class'] = 'class_III'  # Default to class_III
    
    # Find indices where 'empty' is True and False
    false_indices = group[group['empty'] == False].index
    true_indices = group[group['empty'] == True].index

    # If there are any False values
    if not false_indices.empty:
        # Classify before the first False as 'class_I'
        first_false_index = false_indices.min()
        group.loc[:first_false_index, 'class'] = 'class_I'  # Everything before the first false
        group.loc[first_false_index, 'class'] = 'class_II'  # The first false

        # Classify from the first False until the next True as 'class_II'
        if not true_indices.empty:
            next_true_index = true_indices[true_indices > first_false_index].min()
            if pd.notna(next_true_index):
                group.loc[first_false_index:next_true_index - 1, 'class'] = 'class_II'
                group.loc[next_true_index:, 'class'] = 'class_III'
            else:
                # If no True follows the False, all remain 'class_II'
                group.loc[first_false_index:, 'class'] = 'class_II'
        else:
            # If no True values at all after the first False
            group.loc[first_false_index:, 'class'] = 'class_II'

    return group

# Apply the final classification function to each group
classified_df_final = original_df.groupby(['patient', 'days'], group_keys=False).apply(classify_group_final)

# Drop the unnecessary column again if present
if 'Unnamed: 3' in classified_df_final.columns:
    classified_df_final = classified_df_final.drop(columns=['Unnamed: 3'])

# Save the updated DataFrame to a new CSV file
#classified_df_final.to_csv('/mnt/data/Change_Final.csv', index=False)

classified_df_final.head()


/var/folders/j5/c5vt47v9695609y1ssl7zjdr0000gn/T/ipykernel_3499/2472011501.py:34: DeprecationWarning: DataFrameGroupBy.apply operated on the grouping columns. This behavior is deprecated, and in a future version of pandas the grouping columns will be excluded from the operation. Either pass `include_groups=False` to exclude the groupings or explicitly select the grouping columns after groupby to silence this warning.
  classified_df_final = original_df.groupby(['patient', 'days'], group_keys=False).apply(classify_group_final)


id  patient           days  \
0  case101_day20_slice_0001  case101  case101_day20   
1  case101_day20_slice_0002  case101  case101_day20   
2  case101_day20_slice_0003  case101  case101_day20   
3  case101_day20_slice_0004  case101  case101_day20   
4  case101_day20_slice_0005  case101  case101_day20   

                                         image_files  spacing_x  spacing_y  \
0  /Users/arahjou/Downloads/uw-madison-gi-tract-i...        1.5        1.5   
1  /Users/arahjou/Downloads/uw-madison-gi-tract-i...        1.5        1.5   
2  /Users/arahjou/Downloads/uw-madison-gi-tract-i...        1.5        1.5   
3  /Users/arahjou/Downloads/uw-madison-gi-tract-i...        1.5        1.5   
4  /Users/arahjou/Downloads/uw-madison-gi-tract-i...        1.5        1.5   

   size_x  size_y  slice segmentation  rle_len  empty    class  
0     266     266    131       [, , ]        0   True  class_I  
1     266     266     32       [, , ]        0   True  class_I  
2     266     266     84       [, , ]        0   True  class_I  
3     266     266     92       [, , ]        0   True  class_I  
4     266     266     24       [, , ]        0   True  class_I

In [6]:
classified_df_final['class'].value_counts()

class
class_II     16545
class_I      14288
class_III     7663
Name: count, dtype: int64

Transfering images into three different folders class_1, class_2 and class_3.

Below is a Python script that uses `pandas` to read the dataframe and `shutil` for copying files to the appropriate directories based on the class specified in the dataframe. This script assumes you're working in a directory that already contains the images and the Python script.


### Notes:
1. **DataFrame Path**: Ensure the path to your CSV file (`'path_to_your_csv_file.csv'`) is correct.
2. **Image Paths**: The script assumes the paths in your dataframe (`'image_files'` column) are absolute or correctly relative to the script's location. If paths are incorrect, it will fail to find and copy the images.
3. **Error Handling**: There is basic error handling for unrecognized classes. You might want to extend this as necessary, especially to handle potential exceptions like `FileNotFoundError` if an image path does not exist.
4. **Directory Setup**: The script checks if the target directories (`class_I`, `class_II`, `class_III`) exist before trying to create them, avoiding errors from repeated directory creation attempts.

Please ensure to adapt paths and possibly column names according to your actual data structure.

In [7]:
import pandas as pd
import os
import shutil

# Assuming you have already loaded your dataframe
# If not, load it here:
# classified_df_final = pd.read_csv('path_to_your_dataframe.csv')

# Folder names are directly based on the class labels
class_folders = {
    'class_I': 'class_I',
    'class_II': 'class_II',
    'class_III': 'class_III'
}

# Create the directories if they do not exist
for folder in class_folders.values():
    os.makedirs(folder, exist_ok=True)

# Function to copy files to the respective class folders
def copy_files(row):
    src_path = row['image_files']
    class_label = row['class']
    if class_label in class_folders:
        dest_path = os.path.join(class_folders[class_label], os.path.basename(src_path))
        try:
            shutil.copy(src_path, dest_path)
            print(f'Copied {src_path} to {dest_path}')
        except FileNotFoundError:
            print(f'File not found: {src_path}')
        except Exception as e:
            print(f'Error copying {src_path}: {e}')s
    else:
        print(f'Class {class_label} not recognized for file {src_path}')

# Apply the function to each row in the dataframe
classified_df_final.apply(copy_files, axis=1)


Copied /Users/arahjou/Downloads/uw-madison-gi-tract-image-segmentation/train/case22/case22_day0/scans/slice_0131_266_266_1.50_1.50.png to class_I/slice_0131_266_266_1.50_1.50.png
Copied /Users/arahjou/Downloads/uw-madison-gi-tract-image-segmentation/train/case22/case22_day0/scans/slice_0032_266_266_1.50_1.50.png to class_I/slice_0032_266_266_1.50_1.50.png
Copied /Users/arahjou/Downloads/uw-madison-gi-tract-image-segmentation/train/case22/case22_day0/scans/slice_0084_266_266_1.50_1.50.png to class_I/slice_0084_266_266_1.50_1.50.png
Copied /Users/arahjou/Downloads/uw-madison-gi-tract-image-segmentation/train/case22/case22_day0/scans/slice_0092_266_266_1.50_1.50.png to class_I/slice_0092_266_266_1.50_1.50.png
Copied /Users/arahjou/Downloads/uw-madison-gi-tract-image-segmentation/train/case22/case22_day0/scans/slice_0024_266_266_1.50_1.50.png to class_I/slice_0024_266_266_1.50_1.50.png
Copied /Users/arahjou/Downloads/uw-madison-gi-tract-image-segmentation/train/case22/case22_day0/scans/sli

0        None
1        None
2        None
3        None
4        None
         ... 
38491    None
38492    None
38493    None
38494    None
38495    None
Length: 38496, dtype: object